A NB to test out the creation of my candle stick graph for page 2 of the application 

In [81]:
from curses import window
import datetime
from os import name
from turtle import mode
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd
import yfinance as yf
import polars as pl
import sqlalchemy as sql
from datetime import date
import numpy as np
from sqlite3 import DatabaseError, OperationalError, ProgrammingError
from yahoofinancials import YahooFinancials

def main():
    # will have to implement checks to prevent sqli just because itll be fun to do so
    ticker = input('enter stock ticker: ').upper().strip()
    stock_data, db_df = get_stock_data(ticker)
    db_df = process_data(stock_data, db_df)
    stock_data['20_day'] = stock_data['Close'].rolling(window=20).mean()
    stock_data['50_day'] = stock_data["Close"].rolling(window=50).mean()
    stock_data['100_day'] = stock_data["Close"].rolling(window=100).mean()
    stock_data['200_day'] = stock_data["Close"].rolling(window=200).mean()
    # find crosses of the 50 day and 200 day 
    stock_data['crossover'] = 0
    stock_data.loc[(stock_data['50_day'] > stock_data['200_day']) & (stock_data['50_day'].shift(1) <= stock_data['200_day'].shift(1)), 'crossover'] = 1
    stock_data.loc[(stock_data['50_day'] < stock_data['200_day']) & (stock_data['50_day'].shift(1) >= stock_data['200_day'].shift(1)), 'crossover'] = -1
    
    
    # Calculate the 20-period Standard Deviation (SD)
    stock_data['SD'] = stock_data['Close'].rolling(window=20).std()
    
    # Calculate the Upper Bollinger Band (UB) and Lower Bollinger Band (LB)
    stock_data['UB'] = stock_data['20_day'] + 2 * stock_data['SD']
    stock_data['LB'] = stock_data['20_day'] - 2 * stock_data['SD']
    
    # Calculate RSI
    delta = stock_data["Close"].diff()
    gain = delta.copy()
    loss = delta.copy()
    gain[gain < 0] = 0
    loss[loss > 0] = 0
    avg_gain = gain.rolling(window=14).mean()
    avg_loss = abs(loss.rolling(window=14).mean())
    rs = avg_gain / avg_loss
    stock_data["rsi"] = 100 - (100 / (1 + rs))
    # Calculate the percentage change
    stock_data['pct_change'] = (stock_data['Close'] - stock_data['Open']) / stock_data['Open'] * 100
    
    # see if price increased or decreased for volume chart 
    stock_data['Increase'] = stock_data['Close'] >= stock_data['Open']

    main_fig = make_main_fig(stock_data, db_df, ticker)
    ta_fig = make_ta_fig(stock_data, ticker)
    bollinger_fig = make_bollinger_fig(stock_data, ticker)
    
    return main_fig, ta_fig, bollinger_fig
def make_main_fig(df, db_df, ticker):
    fig = go.Figure()
    fig.add_trace(go.Candlestick(x=df.index,
                open=df['Open'],
                high=df['High'],
                low=df['Low'],
                close=df['Close'] , 
                name=f'{ticker} Stock Price'))
    # Calculate total percentage change
    total_pct_change = ((df['Close'].iloc[-1] - df['Close'].iloc[0]) / df['Close'].iloc[0]) * 100
    fig.add_trace(go.Scatter(x=df.index, y=df['50_day'], mode='lines', name='50 Day MA'))
    fig.add_trace(go.Scatter(x=df.index, y=df['100_day'], mode='lines', name='100 Day MA'))
    fig.add_trace(go.Scatter(x=df.index, y=df['200_day'], mode='lines', name='200 Day MA'))
    fig = add_crosses(df, fig)
    fig = add_insider_trace(fig, db_df)
    
     # Add annotation for total percentage change
    fig.add_annotation(x=df.index[-1],
                    y=max(df['High']),
                    text=f"Total Change: {total_pct_change:.2f}%",
                    showarrow=False)
    fig.update_layout(
        xaxis=dict(
            rangeslider=dict(visible=False)
        )
    )
    return fig
    
def add_crosses(df, fig):
    golden_crosses = go.Scatter(
        x=df[df['crossover'] == 1].index,
        y=df[df['crossover'] == 1]['50_day'],
        mode='markers',
        marker=dict(
            size=12,
            color="green",
            line=dict(width=2, color="white")
        ),
        name="Golden Cross"
    )

    death_crosses = go.Scatter(
        x=df[df['crossover'] == -1].index,
        y=df[df['crossover'] == -1]['50_day'],
        mode='markers',
        marker=dict(
            size=12,
            color="red",
            line=dict(width=2, color="white")
        ),
        name="Death Cross"
    )

    # Add the scatter plots to the figure
    fig.add_trace(golden_crosses)
    fig.add_trace(death_crosses)
    return fig
def make_ta_fig(df, ticker):
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True, row_heights=[.5, .5]) 
    
    # Add RSI plot
    fig.add_trace(go.Scatter(x=df.index, y=df["rsi"], name="RSI"))
    fig.add_shape(type="line", x0=df.index[0], y0=70, x1=df.index[-1], y1=70, line=dict(color="red", dash="dash"))
    fig.add_shape(type="line", x0=df.index[0], y0=30, x1=df.index[-1], y1=30, line=dict(color="green", dash="dash"))
    
    volume_df = add_weekly_volume(df)
    # Create the volume histogram
    fig.add_trace(go.Bar(x=volume_df['week'],
                y=volume_df['Volume'],
                marker_color=np.where(df['Increase'], 'green', 'red'),
                name="Weekly Volume"), row=2, col=1)
    
    
   
    fig.update_layout(height=500, xaxis_rangeslider_visible=False)
    fig.update_xaxes(showticklabels=True, row=1, col=1)
    fig.update_xaxes(showticklabels=True, row=2, col=1)

    return fig

def make_bollinger_fig(df, ticker):
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df.index, y=df['Close'], mode='lines', name='Stock Price', line=dict(color='black')))
    fig.add_trace(go.Scatter(x=df.index, y=df['LB'], mode='lines', name='Lower Bollinger Band', line=dict(color='red')))
    fig.add_trace(go.Scatter(x=df.index, y=df['UB'], mode='lines', name='Upper Bollinger Band', fill='tonexty', line=dict(color='green')))
    fig.add_trace(go.Scatter(x=df.index, y=df['20_day'], mode='lines', name='Middle Band', line=dict(color='blue')))
    
    fig.show()
    return fig
def add_weekly_volume(stock_data):
    volume_df = pd.DataFrame(stock_data['Volume'])
    volume_df.set_index(stock_data.index, inplace=True)
    # Create a 'week' column
    volume_df['week'] = volume_df.index.to_period('W')
    # Group by week and sum volume
    monthly_data = volume_df.groupby('week')['Volume'].sum().reset_index()
    # Convert PeriodIndex to Timestamp
    monthly_data['week'] = monthly_data['week'].dt.to_timestamp()
    
    return monthly_data
    
def process_data(stock_data, db_df) -> pd.DataFrame:
    # get all rows where stock splits are not = 0
    split = stock_data[stock_data['Stock Splits'] != 0]
    # if there are stock splits -> change the price per share to that stock close price on that given day (thus reflecting the stock split)
    if len(split) > 0:
        for index, row in db_df.iterrows():
            try:
                db_df.at[index, 'TRANS_PRICEPERSHARE'] = round(stock_data.loc[row['FILING_DATE'], 'Close'], 2)
            except KeyError:
                db_df.drop(index)
    return db_df

def add_insider_trace(fig, db_df):
    # Filter the DataFrame into buy and sell DataFrames
    df_buy = db_df[db_df["TRANS_ACQUIRED_DISP_CD"] == "A"]
    df_sell = db_df[db_df["TRANS_ACQUIRED_DISP_CD"] == "D"]

    # create a scatter plot for the insider trading info:
    insider_buy = go.Scatter(
        x=df_buy["FILING_DATE"],
        y=df_buy[
            "TRANS_PRICEPERSHARE"
        ],  # stock_data.loc[db_df['FILING_DATE'], 'Close'],
        mode="markers",
        marker=dict(color="green", size=8, opacity=0.7),
        name="Insider Buys",
        hovertext=db_df.apply(
            lambda row: f"Insider Transaction Info:<br>Shares:{row['TRANS_SHARES']}<br>Avg Cost: ${row['TRANS_PRICEPERSHARE']}<br>Filed on {row['FILING_DATE']}",
            axis=1,
        ),
        hoverinfo="text",
        showlegend=True,
        visible='legendonly'
       
        
    )
    insider_sell = go.Scatter(
        x=df_sell["FILING_DATE"],
        y=df_sell[
            "TRANS_PRICEPERSHARE"
        ],  # stock_data.loc[db_df['FILING_DATE'], 'Close'],
        mode="markers",
        marker=dict(color="red", size=8, opacity=0.7),
        name="Insider Sales",
        hovertext=db_df.apply(
            lambda row: f"Insider Transaction Info:<br>Shares:{row['TRANS_SHARES']}<br>Avg Cost: ${row['TRANS_PRICEPERSHARE']}<br>Filed on {row['FILING_DATE']}",
            axis=1,
        ),
        hoverinfo="text",
        showlegend=True,
        visible='legendonly'
    )
    # Add traces to the figure
    fig.add_trace(insider_buy)
    fig.add_trace(insider_sell)
    return fig
def get_stock_data(ticker_input):
    # will have to implement checks to prevent sqli just because itll be fun to do so
    ticker = ticker_input.upper().strip()

    try:
        engine = sql.create_engine(
            "sqlite:////home/kole/pythonStuff/dataAnalyticsProj/real.db"
        )
    except (OperationalError, TimeoutError, sql.exc.ArgumentError, ProgrammingError):
        exit('Failed to connect to database', 1)
    con = engine.connect()
    query = f'SELECT * FROM insider_data WHERE ISSUERTRADINGSYMBOL = "{ticker}"'
    try:
        # initialize dataframe with results from the query
        db_df = pd.read_sql(query, con)
    except (DatabaseError, OperationalError):
        exit('Error reading from database... is your input a valid stock?', 1)

    if len(db_df) == 0:
        exit(f'No transactions found for {ticker}', 1)
    # access oldest avail insider transaction date
    oldest_date = db_df["FILING_DATE"].min()
    # subtract 2 years from oldest inside trade
    oldest_date = (
        datetime.datetime.strptime(oldest_date, "%Y-%m-%d")
        - datetime.timedelta(days=365 * 2)
    ).date()
    todays_date = date.today().strftime("%Y-%m-%d")
    # get stock data on the daily timeframe from the oldest avail insider (actions=True gives us info about stock split)
    stock_data = yf.download(ticker, start=oldest_date, end=todays_date, actions=True)
    return stock_data, db_df
    
if __name__ == '__main__':
    main()
    

[*********************100%%**********************]  1 of 1 completed
